In [53]:
# Tentativa de Scraping no Site QuintoAndar
# Camila Junqueira
# Gabriel Nasser
# Rafaela Alexandre

import requests
from bs4 import BeautifulSoup
import pandas as pd
import json
import re
import time
from selenium import webdriver
from selenium.webdriver.common.by import By

In [54]:
def getDadosCEP(cep):
		url = (f'http://www.viacep.com.br/ws/{cep}/json')
		
		req = requests.get(url)
		if req.status_code == 200:
			dados_json = json.loads(req.text)
			return dados_json
		else:
			print('Erro ao buscar CEP')

In [55]:
meu_cep = "04078012"
dados = getDadosCEP(meu_cep)
bairro = dados['bairro']
dados

{'cep': '04078-012',
 'logradouro': 'Avenida Divino Salvador',
 'complemento': 'de 501/502 a 799/800',
 'unidade': '',
 'bairro': 'Planalto Paulista',
 'localidade': 'São Paulo',
 'uf': 'SP',
 'estado': 'São Paulo',
 'regiao': 'Sudeste',
 'ibge': '3550308',
 'gia': '1004',
 'ddd': '11',
 'siafi': '7107'}

In [56]:
bairro = bairro.replace(" ", "-").lower()
bairro

'planalto-paulista'

In [57]:
qa = "https://www.quintoandar.com.br/comprar/imovel/{bairro}-sao-paulo-sp-brasil"

In [60]:
def scraper(bairro):
    driver = webdriver.Chrome()

    driver.get('https://www.quintoandar.com.br/comprar/imovel/planalto-paulista-sao-paulo-sp-brasil')
    time.sleep(5)

    for i in range(8):
        try:
            ver_mais_button = driver.find_element(By.XPATH, "//button[contains(text(), 'Ver mais')]")
            ver_mais_button.click()  # Clica no botão
            time.sleep(3)  # Aguarde o conteúdo carregar após o clique
        except:
            pass

    html_content = driver.page_source
    soup = BeautifulSoup(html_content, 'html.parser')
    soup = soup.find('html')
    soup = soup.prettify()
    return soup

In [61]:
moema = scraper(bairro)

In [62]:
soup = BeautifulSoup(moema, 'html.parser')
teste = soup.find_all("div", class_="_2pfuCF")

In [63]:
valor = teste[0].find("h3", class_="EqjlRj").text
valor = re.sub(r'\D', '', valor)
valor

'750000'

In [64]:
m2 = teste[0].find("h3", class_="o6Ojuq").text
m2.split("m²")[0].split(" ")[-2]


'300'

In [65]:
def find_preco_imovel(imovel):
    valor = imovel.find("h3", class_="EqjlRj").text
    return re.sub(r'\D', '', valor)

In [66]:
find_preco_imovel(teste[0])

'750000'

In [67]:
def find_m2_imovel(imovel):
    alt = imovel.find("h3", class_="o6Ojuq").text
    return alt.split("m²")[0].split(" ")[-2]
    

In [68]:
find_m2_imovel(teste[0])

'300'

In [69]:
for i in range(0, 10):
    print("Preco: " + find_preco_imovel(teste[i]))
    print("m2: " + find_m2_imovel(teste[i]))
    print("_"*10)

Preco: 750000
m2: 300
__________
Preco: 387000
m2: 50
__________
Preco: 720000
m2: 160
__________
Preco: 800000
m2: 131
__________
Preco: 660000
m2: 90
__________
Preco: 610000
m2: 95
__________
Preco: 799000
m2: 120
__________
Preco: 780000
m2: 140
__________
Preco: 460000
m2: 96
__________
Preco: 800000
m2: 120
__________


In [15]:
import sqlite3

In [18]:
conn = sqlite3.connect('data.db')
cursor = conn.cursor()

In [19]:
cursor.execute('''
CREATE TABLE IF NOT EXISTS data (
    id INTEGER PRIMARY KEY AUTOINCREMENT,
    cep TEXT NOT NULL,
    bairro TEXT NOT NULL,
    cidade TEXT NOT NULL,
    estado TEXT NOT NULL,
    regiao TEXT NOT NULL,
    preco FLOAT NOT NULL,
    m2 FLOAT NOT NULL,
    preco_m2 FLOAT NOT NULL
)
''')

In [22]:
def create_table():
    cursor.execute('''
    CREATE TABLE IF NOT EXISTS data (
        id INTEGER PRIMARY KEY AUTOINCREMENT,
        cep TEXT NOT NULL,
        bairro TEXT NOT NULL,
        cidade TEXT NOT NULL,
        estado TEXT NOT NULL,
        regiao TEXT NOT NULL,
        preco FLOAT NOT NULL,
        m2 FLOAT NOT NULL,
        preco_m2 FLOAT NOT NULL
    )
    ''')

In [23]:
def add_data(cep, bairro, cidade, estado, regiao, preco, m2, preco_m2):
    cursor.execute('''
    INSERT INTO data (cep, bairro, cidade, estado, regiao, preco, m2, preco_m2) VALUES (?, ?, ?, ?, ?, ?, ?, ?)
    ''', (cep, bairro, cidade, estado, regiao, preco, m2, preco_m2))
    conn.commit()

In [24]:
def remove_data(id):
    cursor.execute('''
    DELETE FROM data WHERE id = ?
    ''', (id,))
    conn.commit()

In [25]:
def get_id(cep):
    cursor.execute('''
    SELECT id FROM data WHERE cep = ?
    ''', (cep,))
    data = cursor.fetchall()
    return data

In [70]:
def extract_data(cep):
    dados = getDadosCEP(cep)
    bairro = dados['bairro']
    cidade = dados['localidade']
    estado = dados['uf']
    regiao = dados['ibge']
    bairro = bairro.replace(" ", "-").lower()
    soup = scraper(bairro)
    soup = BeautifulSoup(soup, 'html.parser')
    imoveis = soup.find_all("div", class_="_2pfuCF")
    for i in range(len(imoveis)-1):
        preco = find_preco_imovel(imoveis[i])
        m2 = find_m2_imovel(imoveis[i])
        preco_m2 = float(preco) / float(m2)
        
        # Check if the data already exists
        cursor.execute('''
        SELECT id FROM data 
        WHERE cep = ? AND bairro = ? AND preco = ? AND m2 = ?
        ''', (cep, bairro, preco, m2))
        
        if cursor.fetchone() is None:
            # Data doesn't exist, so insert it
            add_data(cep, bairro, cidade, estado, regiao, preco, m2, preco_m2)

In [71]:
extract_data("04078012")

AttributeError: 'NoneType' object has no attribute 'text'

In [35]:
def delete_all():
    cursor.execute('''
    DELETE FROM data
    ''')
    conn.commit()

In [41]:
teste = scraper("moema")

In [43]:
from pprint import pprint


pprint(teste)

('<html lang="pt-BR">\n'
 ' <head>\n'
 '  <meta charset="utf-8"/>\n'
 '  <meta content="width=device-width, initial-scale=1" name="viewport"/>\n'
 '  <meta content="yes" name="apple-mobile-web-app-capable"/>\n'
 '  <meta content="QuintoAndar" name="apple-mobile-web-app-title"/>\n'
 '  <meta content="default" name="apple-mobile-web-app-status-bar-style"/>\n'
 '  <link '
 'href="https://cozy-assets.quintoandar.com.br/cozy-static/v1/latest/launcher-icons/ic_launcher_ios_120x120.png" '
 'rel="apple-touch-icon"/>\n'
 '  <link '
 'href="https://cozy-assets.quintoandar.com.br/cozy-static/v1/latest/launcher-icons/ic_launcher_ios_152x152.png" '
 'rel="apple-touch-icon" sizes="152x152"/>\n'
 '  <link '
 'href="https://cozy-assets.quintoandar.com.br/cozy-static/v1/latest/launcher-icons/ic_launcher_ios_167x167.png" '
 'rel="apple-touch-icon" sizes="167x167"/>\n'
 '  <link '
 'href="https://cozy-assets.quintoandar.com.br/cozy-static/v1/latest/launcher-icons/ic_launcher_ios_180x180.png" '
 'rel="app

<html lang="pt-BR"><head><style>.LGLeeN-keyboard-shortcuts-view{display:-webkit-box;display:-webkit-flex;display:-moz-box;display:-ms-flexbox;display:flex}.LGLeeN-keyboard-shortcuts-view table,.LGLeeN-keyboard-shortcuts-view tbody,.LGLeeN-keyboard-shortcuts-view td,.LGLeeN-keyboard-shortcuts-view tr{background:inherit;border:none;margin:0;padding:0}.LGLeeN-keyboard-shortcuts-view table{display:table}.LGLeeN-keyboard-shortcuts-view tr{display:table-row}.LGLeeN-keyboard-shortcuts-view td{-moz-box-sizing:border-box;box-sizing:border-box;display:table-cell;color:#000;padding:6px;vertical-align:middle;white-space:nowrap}.LGLeeN-keyboard-shortcuts-view td:first-child{text-align:end}.LGLeeN-keyboard-shortcuts-view td kbd{background-color:#e8eaed;border-radius:2px;border:none;-moz-box-sizing:border-box;box-sizing:border-box;color:inherit;display:inline-block;font-family:Google Sans Text,Roboto,Arial,sans-serif;line-height:16px;margin:0 2px;min-height:20px;min-width:20px;padding:2px 4px;positio